# Web scraping of Google Scholar: parts 13-16

The following code performs web scraping of Google Scholar using the Python libraries Beautiful Soup and Requests. Scraping papers and co-authors is our main objective.

In [1]:
import numpy as np
import pandas as pd

import requests
import time
from time import sleep
from datetime import datetime
from random import randint

import os

from bs4 import BeautifulSoup
import lxml

In [2]:
# Create results folder
route0 = "../web_scraping_data"

if not os.path.exists(route0):
    os.mkdir(route0)

## Load HCPs

In [3]:
# Load the file with HCP data
hcp_df = pd.read_excel("../novartis_data/BC & Melanoma targets Sweden.xlsx")

# Detect copyrights, it's separated by NA line
ind_cpr = hcp_df.loc[pd.isna(hcp_df["Name"]), :].index[0]

# Remove copyrights and duplicates
hcp_names_all = pd.Series(hcp_df["Name"].head(ind_cpr).unique())

## Querying Google Scholar using Beautiful Soup and Requests

Since we do the scraping of Google Scholar not in one block, but in 16 blocks of 13 HCPs each, we now write a function that does the scraping for any single of the 16 blocks.

In [5]:
def gs_bs_scraping(hcp_names, position):

    start_time_d = datetime.now()
    start_time_t = time.time()

    papers_df = []

    for i in range(len(hcp_names)): # Level: HCPs
        results_num = 0
        for j in [0,10,20]: # Level: Page
            sleep(randint(1,5))
            name_i = hcp_names.loc[i]
            query_i = '"{}"'.format(name_i) # put the doctor's name in quotes 
            print(f"{(position - 1)*len(hcp_names) + i + 1}/{len(hcp_names_all)} --- {query_i}")
            print(f"{j + 1}-{j + 10}")

            headers = {
            'User-agent':
            "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/70.0.3538.102 Safari/537.36 Edge/18.19582"
            }

            proxies = {
            'http': os.getenv('HTTP_PROXY')
            }

            params = {
            "q": query_i, 
            "hl": "en",
            "start": j
            }

            html = requests.get('https://scholar.google.com/scholar', headers=headers, params=params, proxies=proxies).text
        
            soup = BeautifulSoup(html, 'lxml')

            # Check how many articles there are
            results_i = soup.select('.gs_ri')
            results_num = results_num + len([x for x in results_i])

            if results_num > 0:
                results_i = soup.select('.gs_ri')
            else:
                results_i = []

            # Loop over retrieved articles
            papers_df_i = []
            for article in results_i: # Level: Articles
                try:
                    dict_i = {
                        "title": article.select_one('.gs_rt').text,
                        "title_link": article.select_one('.gs_rt a')['href'],
                        "authors" : article.select_one('.gs_a').text.split("- ")[0],
                        "publications" : article.select_one('.gs_a').text.split("- ")[1],
                        "snippet" : article.select_one('.gs_rs').text
                    }
                except:
                    pass

                df_i = pd.DataFrame.from_dict([dict_i])
                df_i["hcp_name"] = name_i
                df_i["num_articles"] = results_num

                papers_df_i.append(df_i)

            if len(papers_df_i) > 0:
                papers_df_i = pd.concat(papers_df_i)
                papers_df.append(papers_df_i)
            else:
                papers_df_i = pd.DataFrame({
                    "hcp_name": [name_i],
                    "num_articles": [results_num]
                })
                papers_df.append(papers_df_i)

        # Store data at the end
        if i == len(hcp_names) - 1:
            print(f"saving file corresponding to results_queries_gs_{position}.csv")
            papers_df = pd.concat(papers_df).reset_index(drop = True)
            papers_df.to_csv(f"{route0}/results_queries_gs_{position}.csv", index = False)
        
    end_time_d = datetime.now()
    end_time_t = time.time()
    duration = end_time_t - start_time_t
    print(f"start time: {start_time_d}")
    print(f"end time: {end_time_d}")
    print(f"duration: {int(np.floor(duration/3600))} hours {(duration-3600*np.floor(duration/3600))/60:.4} minutes")

### Part 13/16: Doctors 157-169

In [6]:
# 13th part
hcp_names = hcp_names_all[156:169].reset_index(drop = True)
hcp_names

0               Jenny Furubrand
1              Lena C Andersson
2               Karin Törnkvist
3                Sofia Wikström
4               Lena Westerberg
5                  Eva Lindblad
6             Liselott Sahlberg
7                  Per Nodbrant
8               Marie Johansson
9                   Sofie Dietl
10    Elisabet Olsson Kivipaasi
11                Karin Nilsson
12          Marianne Pettersson
dtype: object

In [13]:
# Run function
gs_bs_scraping(hcp_names, 13)

157/208 --- "Jenny Furubrand"
1-10
157/208 --- "Jenny Furubrand"
11-20
157/208 --- "Jenny Furubrand"
21-30
158/208 --- "Lena C Andersson"
1-10
158/208 --- "Lena C Andersson"
11-20
158/208 --- "Lena C Andersson"
21-30
159/208 --- "Karin Törnkvist"
1-10
159/208 --- "Karin Törnkvist"
11-20
159/208 --- "Karin Törnkvist"
21-30
160/208 --- "Sofia Wikström"
1-10
160/208 --- "Sofia Wikström"
11-20
160/208 --- "Sofia Wikström"
21-30
161/208 --- "Lena Westerberg"
1-10
161/208 --- "Lena Westerberg"
11-20
161/208 --- "Lena Westerberg"
21-30
162/208 --- "Eva Lindblad"
1-10
162/208 --- "Eva Lindblad"
11-20
162/208 --- "Eva Lindblad"
21-30
163/208 --- "Liselott Sahlberg"
1-10
163/208 --- "Liselott Sahlberg"
11-20
163/208 --- "Liselott Sahlberg"
21-30
164/208 --- "Per Nodbrant"
1-10
164/208 --- "Per Nodbrant"
11-20
164/208 --- "Per Nodbrant"
21-30
165/208 --- "Marie Johansson"
1-10
165/208 --- "Marie Johansson"
11-20
165/208 --- "Marie Johansson"
21-30
166/208 --- "Sofie Dietl"
1-10
166/208 --- "Sofie

In [5]:
results_queries_gs_13 = pd.read_csv(f"{route0}/results_queries_gs_13.csv")
results_queries_gs_13

title  \
0    [HTML][HTML] Palliativ vård, cytostatikabehand...   
1                                                  NaN   
2                                                  NaN   
3    Our experience using the vertical rectus abdom...   
4    Escherichia coli high cell density fed batch c...   
5          [PDF][PDF] Intensive Care of Burns Patients   
6          [PDF][PDF] Intensive Care of Burns Patients   
7           [BOOK][B] Clinical Intensive Care Medicine   
8                                                  NaN   
9                                                  NaN   
10   Faktorer som förhindrar nutritionsvårdsprocess...   
11   Higher rate of SARS-CoV-2 IgG seropositivity i...   
12   Biochemical and epidemiological studies of ear...   
13                                                 NaN   
14                                                 NaN   
15   [HTML][HTML] Stress ecology in Fucus: abiotic,...   
16   Structure and diversity of invertebrate commun...   
17   [HTML][HTML] Increased chemical resistance exp...   
18   [HTML][HTML] Distribution differences and acti...   
19   [PDF][PDF] Chemical settlement inhibition vers...   
20   Invasion of a habitat-forming seaweed: effects...   
21   [HTML][HTML] Introduction of Asian strains and...   
22   [HTML][HTML] Classification of aquatic macrove...   
23   Tropical seaweed beds as important habitats fo...   
24   [HTML][HTML] Effects of boat traffic and moori...   
25   Scale‐dependent influence of environmental var...   
26   Tropical seaweed beds are important habitats f...   
27   The Baltic Health Index (BHI): Assessing the s...   
28   [PDF][PDF] Fritidsbåtars påverkan på grunda ku...   
29   Species-rich Scandinavian grasslands are inher...   
30   [HTML][HTML] Environmental compensation for bi...   
31   [HTML][HTML] Extensive spread of farmed seawee...   
32   Effects of water exchange and vegetation on th...   
33   [HTML][HTML] Effects of plant morphology on sm...   
34   [PDF][PDF] Higher resistance to herbivory in i...   
35   [PDF][PDF] Effekter av bottentrålning på ekosy...   
36   [PDF][PDF] Fouling mediates grazing: intertwin...   
37   [HTML][HTML] Limitations of using blue mussel ...   
38   Establishment of the exotic species Fucus evan...   
39   Sea floor classification with satellite data a...   
40   [PDF][PDF] Letter to editor regarding Kotta et...   
41   [PDF][PDF] Taxon composition and food-web stru...   
42   [HTML][HTML] Mapping and evaluating Marine Pro...   
43     [PDF][PDF] Var finns den frilevande blåstången?   
44   [PDF][PDF] Divergent ecological strategies det...   
45   Working conditions and family situation in rel...   
46   Det rika barnet: Tio förskollärares uppfattnin...   
47   [BOOK][B] Flickor och pojkar med Aspergers syn...   
48   [CITATION][C] Hälsofrämjande beteende utanför ...   
49   [CITATION][C] Suggestopedi och koncentration: ...   
50            Projekt: Hästkrafter för entreprenörskap   
51   Promoting a safety climate and safety activiti...   
52   Screening of germline mutations in the CDKN2A ...   
53                                        Halle au Blé   
54   CDKN2A germ-line mutations in individuals with...   
55                [BOOK][B] Det ideologiska landskapet   
56                [BOOK][B] Det ideologiska landskapet   
57   Den Potentiella Risken med Riskkapital-En stud...   
58   Den Potentiella Risken med Riskkapital-En stud...   
59   [PDF][PDF] Coexpression of MTH1 and PMS2 is as...   
60   Phenocopies in melanoma-prone families with ge...   
61   [HTML][HTML] Cancer risks and survival in pati...   
62   High risk of tobacco-related cancers in CDKN2A...   
63   [HTML][HTML] Main results of the losartan vers...   
64   [HTML][HTML] Extracellular microvesicle microR...   
65   CDKN2a mutation‐negative melanoma families hav...   
66   [HTML][HTML] CM-Score: a validated scoring sys...   
67   Impact of modern systemic therapies and clinic...   
68   Inflammation and apolipoproteins are poten

Wait at least 30 minutes.

### Part 14/16: Doctors 170-182

In [15]:
# 14th part
hcp_names = hcp_names_all[169:182].reset_index(drop = True)
hcp_names

0         Marinette Berglund
1     Sara Margareta Ekenbro
2            Lena Samuelsson
3         Margareth Schoultz
4              Hervor Gramén
5             Mari Johansson
6           Karin Samuelsson
7         Lise-Lotte Jönsson
8                Malin Ståhl
9                  Lena Berg
10           Camilla Persson
11              Marie Boberg
12         Pernilla Karlsson
dtype: object

In [16]:
# Run function
gs_bs_scraping(hcp_names, 14)

170/208 --- "Marinette Berglund"
1-10
170/208 --- "Marinette Berglund"
11-20
170/208 --- "Marinette Berglund"
21-30
171/208 --- "Sara Margareta Ekenbro"
1-10
171/208 --- "Sara Margareta Ekenbro"
11-20
171/208 --- "Sara Margareta Ekenbro"
21-30
172/208 --- "Lena Samuelsson"
1-10
172/208 --- "Lena Samuelsson"
11-20
172/208 --- "Lena Samuelsson"
21-30
173/208 --- "Margareth Schoultz"
1-10
173/208 --- "Margareth Schoultz"
11-20
173/208 --- "Margareth Schoultz"
21-30
174/208 --- "Hervor Gramén"
1-10
174/208 --- "Hervor Gramén"
11-20
174/208 --- "Hervor Gramén"
21-30
175/208 --- "Mari Johansson"
1-10
175/208 --- "Mari Johansson"
11-20
175/208 --- "Mari Johansson"
21-30
176/208 --- "Karin Samuelsson"
1-10
176/208 --- "Karin Samuelsson"
11-20
176/208 --- "Karin Samuelsson"
21-30
177/208 --- "Lise-Lotte Jönsson"
1-10
177/208 --- "Lise-Lotte Jönsson"
11-20
177/208 --- "Lise-Lotte Jönsson"
21-30
178/208 --- "Malin Ståhl"
1-10
178/208 --- "Malin Ståhl"
11-20
178/208 --- "Malin Ståhl"
21-30
179/208

In [6]:
results_queries_gs_14 = pd.read_csv(f"{route0}/results_queries_gs_14.csv")
results_queries_gs_14

title  \
0    Objective measurements of radiotherapy‐induced...   
1                                                  NaN   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
5                                                  NaN   
6    [HTML][HTML] Genome-wide association study ide...   
7    [HTML][HTML] Identification of 15 new psoriasi...   
8    Stress and well‐being among parents of childre...   
9    [HTML][HTML] SLC9A6 mutations cause X-linked m...   
10   Autism spectrum conditons in myotonic dystroph...   
11   Psoriasis susceptibility locus in chromosome r...   
12   [HTML][HTML] Mutations in PROSC disrupt cellul...   
13   Identification of a psoriasis susceptibility c...   
14   Differential Activation of Lung-specific Genes...   
15   A genome-wide search for genes predisposing to...   
16   [HTML][HTML] Meta-analysis of genome-wide stud...   
17   Effects on airways of short-term exposure to t...   
18   [HTML][HTML] Depression in myotonic dystrophy ...   
19   Multiplex Ligation-Dependent Probe Amplificati...   
20   Genome-wide linkage analysis of Scandinavian a...   
21   The CTLA4/CD28 gene region on chromosome 2q33 ...   
22   [HTML][HTML] Surfactant protein A and albumin ...   
23   Analysis of three suggested psoriasis suscepti...   
24   Association of psoriasis to PGLYRP and SPRR ge...   
25   CTNND2—a candidate gene for reading problems a...   
26   Characterization of the human lipoprotein lipa...   
27   [HTML][HTML] An emerging phenotype of Xq22 mic...   
28   [HTML][HTML] Centrosomal Localization of the P...   
29   [HTML][HTML] Insulin can enhance GLUT4 gene ex...   
30   UBE2A deficiency syndrome: A report of two unr...   
31   [PDF][PDF] Stronger association with HLA-Cw6 t...   
32   [HTML][HTML] Collecting a set of psoriasis fam...   
33   [HTML][HTML] Analysis of chromosome 5q31–32 an...   
34   Preschool children's experience and understand...   
35   On the significance of craniosynostosis in a c...   
36                                                 NaN   
37                                                 NaN   
38                                                 NaN   
39   [BOOK][B] Taschenwörterbuch für Botaniker und ...   
40                                                 NaN   
41                                                 NaN   
42          Esimiehen heikot taidot tunneälyn käytössä   
43   Vem får välja i förskola och skola: En fenomen...   
44   [CITATION][C] Drug‐induced hepatic injury in S...   
45   Vägen till en hållbar citylogistik: En kvalita...   
46   Bestämning av den protolytiska aktiviteten hos...   
47   " Duktig flicka": En intervjustudie om vad i l...   
48   [PDF][PDF] Sairaanhoitajan työ paperittomien k...   
49         Esimies koetun oikeudenmukaisuuden lähteenä   
50   DET DRABBAR ANDRA, INTE MIG: En litteraturstud...   
51   Mindre bolags tilläggsupplysningar: En statist...   
52   [PDF][PDF] Trust in wholesaler-retailer relati...   
53   Läsinlärning-en fallstudie från barnens perspe...   
54     [HTML][HTML] Agila metoders påverkan på testare   
55   Aktivering av unga socialbidragstagare: upplev...   
56    Mikrobryggerier: Etableringsfaktorer vid nystart   
57    Mikrobryggerier: Etableringsfaktorer vid nystart   
58    Mikrobryggerier: Etableringsfaktorer vid nystart   
59   [CITATION][C] Trendgympa: En kartläggande unde...   
60   [CITATION][C] Kvinnliga förövare: olika myndig...   
61   [CITATION][C] Mindfulnessilla työhyvinvointia?...   
62   [CITATION][C] Mindfulnessilla työhyvinvointia?...   
63   [CITATION][C] Mindfulnessilla työhyvinvointia?...   
64                        [CITATION][C] V-som i vinter   
65   [PDF][PDF] Korset och kapitälet: De fornkristn...   
66   [PDF][PDF] Mark C. Mattes: Martin Luther´ s Th...   
67   [PDF][PDF] Mark C. Mattes: Martin Luther´ s Th...   
68   [PDF][PDF] Kroppen i skandinavisk forkynne

Wait at least 30 minutes.

### Part 15/16: Doctors 183-195

In [18]:
# 15th part
hcp_names = hcp_names_all[182:195].reset_index(drop = True)
hcp_names

0          Lotta Henriksson
1           Karin Johansson
2        Charlotta Pramsten
3             Lola Svensson
4             Daniel Giglio
5        Elsy-Britt Schildt
6     Erika Isaksson Friman
7     Eva Djureen Mårtenson
8                   Lars Ny
9          Harriet Axelsson
10          Gustav Silander
11               Lisa Rydén
12           Carina Larsson
dtype: object

In [19]:
# Run function
gs_bs_scraping(hcp_names, 15)

183/208 --- "Lotta Henriksson"
1-10
183/208 --- "Lotta Henriksson"
11-20
183/208 --- "Lotta Henriksson"
21-30
184/208 --- "Karin Johansson"
1-10
184/208 --- "Karin Johansson"
11-20
184/208 --- "Karin Johansson"
21-30
185/208 --- "Charlotta Pramsten"
1-10
185/208 --- "Charlotta Pramsten"
11-20
185/208 --- "Charlotta Pramsten"
21-30
186/208 --- "Lola Svensson"
1-10
186/208 --- "Lola Svensson"
11-20
186/208 --- "Lola Svensson"
21-30
187/208 --- "Daniel Giglio"
1-10
187/208 --- "Daniel Giglio"
11-20
187/208 --- "Daniel Giglio"
21-30
188/208 --- "Elsy-Britt Schildt"
1-10
188/208 --- "Elsy-Britt Schildt"
11-20
188/208 --- "Elsy-Britt Schildt"
21-30
189/208 --- "Erika Isaksson Friman"
1-10
189/208 --- "Erika Isaksson Friman"
11-20
189/208 --- "Erika Isaksson Friman"
21-30
190/208 --- "Eva Djureen Mårtenson"
1-10
190/208 --- "Eva Djureen Mårtenson"
11-20
190/208 --- "Eva Djureen Mårtenson"
21-30
191/208 --- "Lars Ny"
1-10
191/208 --- "Lars Ny"
11-20
191/208 --- "Lars Ny"
21-30
192/208 --- "Har

In [7]:
results_queries_gs_15 = pd.read_csv(f"{route0}/results_queries_gs_15.csv")
results_queries_gs_15

title  \
0    Idiotype immunization combined with granulocyt...   
1    [HTML][HTML] Augmentation of the immune respon...   
2    Idiotype immunity (natural and vaccine-induced...   
3    Ravitsemuksen ja liikunnan vaikutukset hedelmä...   
4    Ravitsemuksen ja liikunnan vaikutukset hedelmä...   
5    Ravitsemuksen ja liikunnan vaikutukset hedelmä...   
6           [PDF][PDF] Föredragningslista Föredragande   
7    Att bli pensionär: övergången från yrkesroll t...   
8    ” Jag skulle inte vilja dö ensam”: sjukhemsper...   
9    Genetic immunotherapy of established tumors wi...   
10   VAD ÄR SVÅRT MED SVÅRA SAMTAL?: En kvalitativ ...   
11   Nedskärningar och besparningar inom äldreomsorgen   
12   Broadened clinical utility of gene gun-mediate...   
13                                                 NaN   
14   Upper‐body morbidity after breast cancer: inci...   
15   Manual lymphatic drainage for lymphedema follo...   
16   A prospective surveillance model for rehabilit...   
17   Effects of compression bandaging with or witho...   
18   A randomized study comparing manual lymph drai...   
19   Low intensity resistance exercise for breast c...   
20   Factors associated with the development of arm...   
21   Breast cancer patients' experiences of lymphoe...   
22   [HTML][HTML] Integrating genome-based informat...   
23   Arm lymphoedema in a cohort of breast cancer s...   
24   Arm lymphoedema, shoulder mobility and muscle ...   
25   Regeneration of European boreal forests: effec...   
26   [HTML][HTML] A lifeworld phenomenological stud...   
27   Multiplex SNP genotyping in pooled DNA samples...   
28   Microarray analysis of immune challenged Droso...   
29   Moving beyond 'aging in place'to understand mi...   
30   [HTML][HTML] Water-based exercise for patients...   
31   Creating possibilities for action in the prese...   
32   [HTML][HTML] Pentoxifylline and vitamin E trea...   
33   Experimental and analytical comparisons of tis...   
34   [PDF][PDF] Threadlike micelles from cetyltrime...   
35   A comparison of long-term effects of scarifica...   
36   UN peacekeeping and protection from sexual vio...   
37   Women's experience of physical activity follow...   
38   Kinetics of the hydration reactions in the cem...   
39   Cross-border spread of blaNDM-1-and blaOXA-48-...   
40   Bone marrow-and adipose tissue-derived mesench...   
41   Lymphedema Quality of Life Inventory (LyQLI)-D...   
42   Experts, entrepreneurs and competence nomads: ...   
43   [PDF][PDF] Interactions between soil scarifica...   
44                                                 NaN   
45                                                 NaN   
46                                                 NaN   
47   Forssman expression on human erythrocytes: bio...   
48   Blood group A1 and A2 revisited: an immunochem...   
49   Point mutations and deletion responsible for t...   
50   Typing for the human Lewis blood group system ...   
51   DNA sequencing and screening for point mutatio...   
52   Determination of Lewis FUT3 gene mutations by ...   
53   Intravenous synthetic αgal saccharides delay h...   
54   [HTML][HTML] Prevalence of antibodies to a new...   
55   The structural basis of blood group A-related ...   
56   Characterisation of the anti-A antibody respon...   
57   Glycolipid-and glycoprotein-based blood group ...   
58   Expression of carbohydrate xenoantigens on por...   
59   Expression of the GBGT1 gene and the forssman ...   
60   An ELISA technique for quantitation of human x...   
61   [CITATION][C] Nomenclature of granulocyte allo...   
62           [BOOK][B] Chemical basis of ABO subgroups   
63             [CITATION][C] Massive Blood Replacement   
64   [CITATION][C] The Use and Quality Control of L...   
65           [CITATION][C] Subject Index Vol. 77, 1999   
66            [CITATION][C] Author Index Vol. 77, 1999   
67                [CITATION][C] Contents Vol. 77, 1999   
68          [CITATION][C] Acknowledgements to R

Wait at least 30 minutes.

### Part 16/16: Doctors 196-208

In [21]:
# 16th part
hcp_names = hcp_names_all[195:208].reset_index(drop = True)
hcp_names

0             Karin Lycknert
1               Niklas Loman
2         Olga Del Val Munoz
3          Olof Bjarnadottir
4            Samuel Rotstein
5               Sara Kinhult
6         Theodoros Foukakis
7            Maria Gränström
8     Ylva Holmgren Stenlund
9                Anna Nyberg
10           Göran Carlstedt
11          Mikael Wallander
12           Frida Jakobsson
dtype: object

In [22]:
# Run function
gs_bs_scraping(hcp_names, 16)

196/208 --- "Karin Lycknert"
1-10
196/208 --- "Karin Lycknert"
11-20
196/208 --- "Karin Lycknert"
21-30
197/208 --- "Niklas Loman"
1-10
197/208 --- "Niklas Loman"
11-20
197/208 --- "Niklas Loman"
21-30
198/208 --- "Olga Del Val Munoz"
1-10
198/208 --- "Olga Del Val Munoz"
11-20
198/208 --- "Olga Del Val Munoz"
21-30
199/208 --- "Olof Bjarnadottir"
1-10
199/208 --- "Olof Bjarnadottir"
11-20
199/208 --- "Olof Bjarnadottir"
21-30
200/208 --- "Samuel Rotstein"
1-10
200/208 --- "Samuel Rotstein"
11-20
200/208 --- "Samuel Rotstein"
21-30
201/208 --- "Sara Kinhult"
1-10
201/208 --- "Sara Kinhult"
11-20
201/208 --- "Sara Kinhult"
21-30
202/208 --- "Theodoros Foukakis"
1-10
202/208 --- "Theodoros Foukakis"
11-20
202/208 --- "Theodoros Foukakis"
21-30
203/208 --- "Maria Gränström"
1-10
203/208 --- "Maria Gränström"
11-20
203/208 --- "Maria Gränström"
21-30
204/208 --- "Ylva Holmgren Stenlund"
1-10
204/208 --- "Ylva Holmgren Stenlund"
11-20
204/208 --- "Ylva Holmgren Stenlund"
21-30
205/208 --- "

In [8]:
results_queries_gs_16 = pd.read_csv(f"{route0}/results_queries_gs_16.csv")
results_queries_gs_16

hcp_name  num_articles  \
0            Karin Lycknert             0   
1            Karin Lycknert             0   
2            Karin Lycknert             0   
3              Niklas Loman            10   
4              Niklas Loman            10   
5              Niklas Loman            10   
6              Niklas Loman            10   
7              Niklas Loman            10   
8              Niklas Loman            10   
9              Niklas Loman            10   
10             Niklas Loman            10   
11             Niklas Loman            10   
12             Niklas Loman            10   
13             Niklas Loman            20   
14             Niklas Loman            20   
15             Niklas Loman            20   
16             Niklas Loman            20   
17             Niklas Loman            20   
18             Niklas Loman            20   
19             Niklas Loman            20   
20             Niklas Loman            20   
21             Niklas Loman            20   
22             Niklas Loman            20   
23             Niklas Loman            30   
24             Niklas Loman            30   
25             Niklas Loman            30   
26             Niklas Loman            30   
27             Niklas Loman            30   
28             Niklas Loman            30   
29             Niklas Loman            30   
30             Niklas Loman            30   
31             Niklas Loman            30   
32             Niklas Loman            30   
33       Olga Del Val Munoz             4   
34       Olga Del Val Munoz             4   
35       Olga Del Val Munoz             4   
36       Olga Del Val Munoz             4   
37       Olga Del Val Munoz             4   
38       Olga Del Val Munoz             4   
39        Olof Bjarnadottir            10   
40        Olof Bjarnadottir            10   
41        Olof Bjarnadottir            10   
42        Olof Bjarnadottir            10   
43        Olof Bjarnadottir            10   
44        Olof Bjarnadottir            10   
45        Olof Bjarnadottir            10   
46        Olof Bjarnadottir            10   
47        Olof Bjarnadottir            10   
48        Olof Bjarnadottir            10   
49        Olof Bjarnadottir            20   
50        Olof Bjarnadottir            20   
51        Olof Bjarnadottir            20   
52        Olof Bjarnadottir            20   
53        Olof Bjarnadottir            20   
54        Olof Bjarnadottir            20   
55        Olof Bjarnadottir            20   
56        Olof Bjarnadottir            20   
57        Olof Bjarnadottir            20   
58        Olof Bjarnadottir            20   
59        Olof Bjarnadottir            21   
60          Samuel Rotstein            10   
61          Samuel Rotstein            10   
62          Samuel Rotstein            10   
63          Samuel Rotstein            10   
64          Samuel Rotstein            10   
65          Samuel Rotstein            10   
66          Samuel Rotstein            10   
67          Samuel Rotstein            10   
68          Samuel Rotstein            10   
69          Samuel Rotstein            10   
70          Samuel Rotstein            20   
71          Samuel Rotstein            20   
72          Samuel Rotstein            20   
73          Samuel Rotstein            20   
74          Samuel Rotstein            20   
75          Samuel Rotstein            20   
76          Samuel Rotstein            20   
77          Samuel Rotstein            20   
78          Samuel Rotstein            20   
79          Samuel Rotstein            20   
80          Samuel Rotstein            30   
81          Samuel Rotstein            30   
82          Samuel Rotstein            30   
83          Samuel Rotstein            30   
84          Samuel Rotstein            30   
85          Samuel Rotstein            30   
86          Samuel Rotstein            30   
87          Samuel Rotstein            30   
88          Sa

Wait at least 30 minutes.

## Stack all 16 dataset and save the final dataset 

Having scraped Google Scholar for all 16 blocks, we finally stack all 16 dataset that we obtained and save it as one dataset.

In [9]:
df_names = []
for i in range(16):
    df_names = df_names + [f"results_queries_gs_{i + 1}"]
    
df_dict = dict()
for df_name in df_names:
    df_dict[df_name] = pd.read_csv(f"{route0}/{df_name}.csv")

In [10]:
df_dict['results_queries_gs_1']

hcp_name  num_articles  \
0              Adel Bader Hamdalla             0   
1              Adel Bader Hamdalla             0   
2              Adel Bader Hamdalla             0   
3                    Aglaia Schiza            10   
4                    Aglaia Schiza            10   
5                    Aglaia Schiza            10   
6                    Aglaia Schiza            10   
7                    Aglaia Schiza            10   
8                    Aglaia Schiza            10   
9                    Aglaia Schiza            10   
10                   Aglaia Schiza            10   
11                   Aglaia Schiza            10   
12                   Aglaia Schiza            10   
13                   Aglaia Schiza            17   
14                   Aglaia Schiza            17   
15                   Aglaia Schiza            17   
16                   Aglaia Schiza            17   
17                   Aglaia Schiza            17   
18                   Aglaia Schiza            17   
19                   Aglaia Schiza            17   
20                   Aglaia Schiza            17   
21           Agneta Nordin Danfors             1   
22           Agneta Nordin Danfors             1   
23           Agneta Nordin Danfors             1   
24         Ahmed Abbas Albu-Kareem             0   
25         Ahmed Abbas Albu-Kareem             0   
26         Ahmed Abbas Albu-Kareem             0   
27                     Alaa Haidar             5   
28                     Alaa Haidar             5   
29                     Alaa Haidar             5   
30                     Alaa Haidar             5   
31                     Alaa Haidar             5   
32                     Alaa Haidar             5   
33                     Alaa Haidar             5   
34                Ana Bosch Campos            10   
35                Ana Bosch Campos            10   
36                Ana Bosch Campos            10   
37                Ana Bosch Campos            10   
38                Ana Bosch Campos            10   
39                Ana Bosch Campos            10   
40                Ana Bosch Campos            10   
41                Ana Bosch Campos            10   
42                Ana Bosch Campos            10   
43                Ana Bosch Campos            10   
44                Ana Bosch Campos            13   
45                Ana Bosch Campos            13   
46                Ana Bosch Campos            13   
47                Ana Bosch Campos            13   
48                Andreas Nearchou            10   
49                Andreas Nearchou            10   
50                Andreas Nearchou            10   
51                Andreas Nearchou            10   
52                Andreas Nearchou            10   
53                Andreas Nearchou            10   
54                Andreas Nearchou            10   
55                Andreas Nearchou            10   
56                Andreas Nearchou            10   
57                Andreas Nearchou            10   
58                Andreas Nearchou            20   
59                Andreas Nearchou            20   
60                Andreas Nearchou            20   
61                Andreas Nearchou            20   
62                Andreas Nearchou            20   
63                Andreas Nearchou            20   
64                Andreas Nearchou            20   
65                Andreas Nearchou            20   
66                Andreas Nearchou            20   
67                Andreas Nearchou            20   
68                Andreas Nearchou            30   
69                Andreas Nearchou            30   
70                Andreas Nearchou            30   
71                Andreas Nearchou            30   
72                Andreas Nearchou            30   
73                Andreas Nearchou            30   
74                Andreas Nearchou            30   
75                Andreas Nearchou            30   
76                Andr

In [11]:
for value in df_dict:
    df_dict[value] = df_dict[value][['hcp_name', 'num_articles', 'title', 'title_link', 'authors', 'publications', 'snippet']]

In [12]:
results_queries_gs = pd.DataFrame()

for i in range(16):
    results_queries_gs = results_queries_gs.append(df_dict[f"results_queries_gs_{i + 1}"], ignore_index=True)
    
results_queries_gs

hcp_name  num_articles  \
0               Adel Bader Hamdalla             0   
1               Adel Bader Hamdalla             0   
2               Adel Bader Hamdalla             0   
3                     Aglaia Schiza            10   
4                     Aglaia Schiza            10   
5                     Aglaia Schiza            10   
6                     Aglaia Schiza            10   
7                     Aglaia Schiza            10   
8                     Aglaia Schiza            10   
9                     Aglaia Schiza            10   
10                    Aglaia Schiza            10   
11                    Aglaia Schiza            10   
12                    Aglaia Schiza            10   
13                    Aglaia Schiza            17   
14                    Aglaia Schiza            17   
15                    Aglaia Schiza            17   
16                    Aglaia Schiza            17   
17                    Aglaia Schiza            17   
18                    Aglaia Schiza            17   
19                    Aglaia Schiza            17   
20                    Aglaia Schiza            17   
21            Agneta Nordin Danfors             1   
22            Agneta Nordin Danfors             1   
23            Agneta Nordin Danfors             1   
24          Ahmed Abbas Albu-Kareem             0   
25          Ahmed Abbas Albu-Kareem             0   
26          Ahmed Abbas Albu-Kareem             0   
27                      Alaa Haidar             5   
28                      Alaa Haidar             5   
29                      Alaa Haidar             5   
30                      Alaa Haidar             5   
31                      Alaa Haidar             5   
32                      Alaa Haidar             5   
33                      Alaa Haidar             5   
34                 Ana Bosch Campos            10   
35                 Ana Bosch Campos            10   
36                 Ana Bosch Campos            10   
37                 Ana Bosch Campos            10   
38                 Ana Bosch Campos            10   
39                 Ana Bosch Campos            10   
40                 Ana Bosch Campos            10   
41                 Ana Bosch Campos            10   
42                 Ana Bosch Campos            10   
43                 Ana Bosch Campos            10   
44                 Ana Bosch Campos            13   
45                 Ana Bosch Campos            13   
46                 Ana Bosch Campos            13   
47                 Ana Bosch Campos            13   
48                 Andreas Nearchou            10   
49                 Andreas Nearchou            10   
50                 Andreas Nearchou            10   
51                 Andreas Nearchou            10   
52                 Andreas Nearchou            10   
53                 Andreas Nearchou            10   
54                 Andreas Nearchou            10   
55                 Andreas Nearchou            10   
56                 Andreas Nearchou            10   
57                 Andreas Nearchou            10   
58                 Andreas Nearchou            20   
59                 Andreas Nearchou            20   
60                 Andreas Nearchou            20   
61                 Andreas Nearchou            20   
62                 Andreas Nearchou            20   
63                 Andreas Nearchou            20   
64                 Andreas Nearchou            20   
65                 Andreas Nearchou            20   
66                 Andreas Nearchou            20   
67                 Andreas Nearchou            20   
68                 Andreas Nearchou            30   
69                 Andreas Nearchou            30   
70                 Andreas Nearchou            30   
71                 Andreas Nearchou            30   
72                 Andreas Nearchou            30   
73                 Andreas Nearchou            30   
74                 Andreas Nearchou            30   

In [8]:
print(f"saving file corresponding to results_queries_gs.csv")
results_queries_gs.to_csv(f"{route0}/results_queries_gs.csv", index = False)

saving file corresponding to results_queries_gs.csv


In [13]:
# Read in data scraped from Google Scholar
results_queries_gs = pd.read_csv(f"{route0}/results_queries_gs.csv")
results_queries_gs.shape    

(3778, 7)

## Results

In [14]:
results_queries_gs

hcp_name  num_articles  \
0               Adel Bader Hamdalla             0   
1               Adel Bader Hamdalla             0   
2               Adel Bader Hamdalla             0   
3                     Aglaia Schiza            10   
4                     Aglaia Schiza            10   
5                     Aglaia Schiza            10   
6                     Aglaia Schiza            10   
7                     Aglaia Schiza            10   
8                     Aglaia Schiza            10   
9                     Aglaia Schiza            10   
10                    Aglaia Schiza            10   
11                    Aglaia Schiza            10   
12                    Aglaia Schiza            10   
13                    Aglaia Schiza            17   
14                    Aglaia Schiza            17   
15                    Aglaia Schiza            17   
16                    Aglaia Schiza            17   
17                    Aglaia Schiza            17   
18                    Aglaia Schiza            17   
19                    Aglaia Schiza            17   
20                    Aglaia Schiza            17   
21            Agneta Nordin Danfors             1   
22            Agneta Nordin Danfors             1   
23            Agneta Nordin Danfors             1   
24          Ahmed Abbas Albu-Kareem             0   
25          Ahmed Abbas Albu-Kareem             0   
26          Ahmed Abbas Albu-Kareem             0   
27                      Alaa Haidar             5   
28                      Alaa Haidar             5   
29                      Alaa Haidar             5   
30                      Alaa Haidar             5   
31                      Alaa Haidar             5   
32                      Alaa Haidar             5   
33                      Alaa Haidar             5   
34                 Ana Bosch Campos            10   
35                 Ana Bosch Campos            10   
36                 Ana Bosch Campos            10   
37                 Ana Bosch Campos            10   
38                 Ana Bosch Campos            10   
39                 Ana Bosch Campos            10   
40                 Ana Bosch Campos            10   
41                 Ana Bosch Campos            10   
42                 Ana Bosch Campos            10   
43                 Ana Bosch Campos            10   
44                 Ana Bosch Campos            13   
45                 Ana Bosch Campos            13   
46                 Ana Bosch Campos            13   
47                 Ana Bosch Campos            13   
48                 Andreas Nearchou            10   
49                 Andreas Nearchou            10   
50                 Andreas Nearchou            10   
51                 Andreas Nearchou            10   
52                 Andreas Nearchou            10   
53                 Andreas Nearchou            10   
54                 Andreas Nearchou            10   
55                 Andreas Nearchou            10   
56                 Andreas Nearchou            10   
57                 Andreas Nearchou            10   
58                 Andreas Nearchou            20   
59                 Andreas Nearchou            20   
60                 Andreas Nearchou            20   
61                 Andreas Nearchou            20   
62                 Andreas Nearchou            20   
63                 Andreas Nearchou            20   
64                 Andreas Nearchou            20   
65                 Andreas Nearchou            20   
66                 Andreas Nearchou            20   
67                 Andreas Nearchou            20   
68                 Andreas Nearchou            30   
69                 Andreas Nearchou            30   
70                 Andreas Nearchou            30   
71                 Andreas Nearchou            30   
72                 Andreas Nearchou            30   
73                 Andreas Nearchou            30   
74                 Andreas Nearchou            30   